### This notebook is the second step/final step toward predicting the event type



__Main Steps__

* _Libraries_: Run requirements.txt to install the required libraries if you haven't already. It is recommended to use a venv.

* _Run first step to generate data_: Run 1_CreateInput.ipynb file to generate the input for our prediction model.

* _Vectorize the data_: The csv data is encoded into vector format.

* _LSTM Model_: The LSTM model is used to perform prediction.

In [1]:
from common import cities, city_keys, years, months
from sklearn.preprocessing import LabelEncoder, StandardScaler
from sklearn.metrics import classification_report
from tensorflow.keras.models import Sequential, load_model
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.layers import LSTM, Dense
import pandas as pd
import numpy as np
import os

2025-04-26 22:46:51.282607: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-04-26 22:46:51.300504: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:467] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1745722011.315273  455518 cuda_dnn.cc:8579] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1745722011.319572  455518 cuda_blas.cc:1407] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
W0000 00:00:1745722011.334784  455518 computation_placer.cc:177] computation placer already registered. Please check linkage and avoid linking 

In [2]:
print(cities, city_keys, years, months)

{'Austin': {'coordinates': [30.079327, -97.968881, 30.596764, -97.504838], 'weather': [(30.079, -97.969), (30.58, -97.969), (30.079, -97.718), (30.33, -97.969), (30.58, -97.718), (30.33, -97.718)], 'sunrise': 'austin-tx', 'timezone': 'US/Central'}, 'LosAngeles': {'coordinates': [33.700615, -118.683511, 34.353627, -118.074559], 'weather': [(34.201, -118.183), (33.7, -118.684), (33.951, -118.684), (34.201, -118.4335), (33.7, -118.183), (33.951, -118.183), (33.7, -118.4335), (33.951, -118.4335), (34.201, -118.684)], 'sunrise': 'los-angeles-ca', 'timezone': 'US/Pacific'}, 'NewYorkCity': {'coordinates': [40.477399, -74.25909, 40.917577, -73.700272], 'weather': [(40.477, -74.259), (40.702, -74.259), (40.477, -73.965), (40.59, -74.259), (40.702, -73.965), (40.59, -73.965)], 'sunrise': 'new-york-ny', 'timezone': 'US/Eastern'}} ['Austin', 'LosAngeles', 'NewYorkCity'] [2017] [6, 9]


In [3]:
def add_sincos_column(df, key, data):
    df[f'{key}_sin'] = np.sin(2 * np.pi * data)
    df[f'{key}_cos'] = np.cos(2 * np.pi * data)

def parse_time(df: pd.DataFrame):
    time_cols = ['StartTime', 'EndTime', 'Sunrise', 'Sunset']
    for column in time_cols:
        if column in df.columns:
            if not np.issubdtype(df[column].dtype, np.datetime64):
                df[column] = pd.to_datetime(df[column])
        else:
            continue

        if 'Sun' not in column:
            days = df[column].dt.day
            add_sincos_column(df, f'{column}_day', (days / 31))

            months = df[column].dt.month
            add_sincos_column(df, f'{column}_month', (months / 12))

            years = df[column].dt.year
            df[f'{column}_year_norm'] = (years - years.min()) / (years.max() - years.min())
        
        seconds = df[column].dt.hour * 3600 + df[column].dt.minute * 60 + df[column].dt.second
        add_sincos_column(df, f'{column}_seconds', (seconds / 86400))

        df.drop(column, axis=1, inplace=True)
    return df

In [4]:
def split_data(df, train_fraction=0.8):
    cut_index = int(len(df) * train_fraction)
    df.sample(frac=1)
    train_df = df.iloc[:cut_index].reset_index(drop=True)
    val_df = df.iloc[cut_index:].reset_index(drop=True)
    return train_df, val_df

In [5]:
def feature_scaling(X_train, X_val):
    scaler = StandardScaler()
    X_train_scaled = scaler.fit_transform(X_train)
    X_val_scaled = scaler.transform(X_val)
    return X_train_scaled, X_val_scaled, scaler

def encode_labels(y_train, y_val):
    label_enc = LabelEncoder()
    y_train_enc = label_enc.fit_transform(y_train)
    y_val_enc = label_enc.transform(y_val)
    y_train_cat = to_categorical(y_train_enc)
    y_val_cat = to_categorical(y_val_enc)
    return y_train_cat, y_val_cat, label_enc, y_train_enc, y_val_enc

In [6]:
def create_sequences(X, y, seq_length):
    sequences_X = []
    sequences_y = []
    for i in range(seq_length - 1, len(X)):
        sequences_X.append(X[i - seq_length + 1: i + 1])
        if y is not None:
            sequences_y.append(y[i])
    sequences_X = np.array(sequences_X)
    sequences_y = np.array(sequences_y) if y is not None else None
    return sequences_X, sequences_y

In [7]:
def build_model(input_shape, num_classes):
    model = Sequential()
    model.add(LSTM(64, input_shape=input_shape))
    model.add(Dense(num_classes, activation='softmax'))
    model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
    return model

def train_model(model, X_train, y_train, X_val, y_val, epochs=50, batch_size=64):
    history = model.fit(X_train, y_train, epochs=epochs, batch_size=batch_size, 
                        validation_data=(X_val, y_val), verbose=1)
    return history

def save_model(model, file_path):
    model.save(file_path)

def load_saved_model(file_path):
    return load_model(file_path)

def evaluate_model(model, X_test, y_test_cat, y_test_enc, label_enc, file_name):
    y_pred_probs = model.predict(X_test)
    y_pred_classes = np.argmax(y_pred_probs, axis=1)
    y_true_classes = y_test_enc[len(y_test_enc) - len(y_pred_classes):]  # align sizes if needed
    with open(file_name, "w") as file:
        file.write(classification_report(y_true_classes, y_pred_classes, labels=np.arange(len(label_enc.classes_)), target_names=label_enc.classes_.astype(str)))

In [8]:
for path in ['../data/output', '../data/print']:
    if not os.path.exists(path):
        os.makedirs(path)

for city in city_keys:
    file_path = f'../data/input/{city}_{years[0]}{months[0]}01_{years[-1]}{months[-1]}01.csv'
    df = pd.read_csv(file_path)
    df = parse_time(df)
    train_df, val_df = split_data(df)
    X_train_df = train_df.drop('Type', axis=1)
    y_train_series = train_df['Type']
    X_val_df = val_df.drop('Type', axis=1)
    y_val_series = val_df['Type']
    X_train_scaled, X_val_scaled, scaler = feature_scaling(X_train_df.values, X_val_df.values)
    y_train_cat, y_val_cat, label_enc, y_train_enc, y_val_enc = encode_labels(y_train_series.values, y_val_series.values)
    
    seq_length = 10
    X_train_seq, y_train_seq = create_sequences(X_train_scaled, y_train_cat, seq_length)
    X_val_seq, y_val_seq = create_sequences(X_val_scaled, y_val_cat, seq_length)
    
    model = build_model(input_shape=(seq_length, X_train_seq.shape[2]), num_classes=y_train_cat.shape[1])
    train_model(model, X_train_seq, y_train_seq, X_val_seq, y_val_seq, epochs=50, batch_size=64)
    model_path = f"../data/output/{city}_{years[0]}{months[0]}01_{years[-1]}{months[-1]}01.h5"
    print_path = f"../data/print/{city}_{years[0]}{months[0]}01_{years[-1]}{months[-1]}01.txt"
    save_model(model, model_path)
    evaluate_model(model, X_val_seq, y_val_seq, y_val_enc, label_enc, print_path)

/tmp/ipykernel_455518/3941543037.py:10: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df[column] = pd.to_datetime(df[column])
/tmp/ipykernel_455518/3941543037.py:10: UserWarning: Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.
  df[column] = pd.to_datetime(df[column])
/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/sklearn/utils/extmath.py:1101: RuntimeWarning: invalid value encountered in divide
  updated_mean = (last_sum + new_sum) / updated_sample_count
/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/sklearn/utils/extmath.py:1106: RuntimeWarning: invalid value encountered in divide
  T = new_sum / new_sample_count
/common/home/ks2025/rutgers/cs551/final_pr

I0000 00:00:1745722014.209860  455518 gpu_device.cc:2019] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 13390 MB memory:  -> device: 0, name: NVIDIA RTX A4000, pci bus id: 0000:a1:00.0, compute capability: 8.6
I0000 00:00:1745722014.210879  455518 gpu_device.cc:2019] Created device /job:localhost/replica:0/task:0/device:GPU:1 with 13390 MB memory:  -> device: 1, name: NVIDIA RTX A4000, pci bus id: 0000:e1:00.0, compute capability: 8.6
/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/keras/src/layers/rnn/rnn.py:200: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


Epoch 1/50


I0000 00:00:1745722015.977087  455919 cuda_dnn.cc:529] Loaded cuDNN version 90300


  1/206 ━━━━━━━━━━━━━━━━━━━━ 5:48 2s/step - accuracy: 0.1719 - loss: nan

...

532/595 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step

574/595 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step

595/595 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step

595/595 ━━━━━━━━━━━━━━━━━━━━ 1s 1ms/step


/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/common/home/ks2025/rutgers/cs551/final_project/.venv/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this beh